In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs

# set the following to True when connected to hardware:
run_on_hw = False

In [3]:
num_channels = 3

# we will map three virtual channels to one physical channel
virtual_awgs = qcs.Channels(range(num_channels), "awgs", True)
virtual_digs = qcs.Channels(range(num_channels), "digs")

# specify our physical channel addresses for AWG, digitizer & downconverter
physical_awg = (1, 1, 1)
physical_dig = (1, 2, 1)
physical_dnc = (1, 3, 1)

In [4]:
lo_frequency = 5e9

mapper = qcs.ChannelMapper()

mapper.add_channel_mapping(
    virtual_awgs, [physical_awg] * num_channels, qcs.InstrumentEnum.M5300AWG
)
mapper.add_channel_mapping(
    virtual_digs, [physical_dig] * num_channels, qcs.InstrumentEnum.M5200Digitizer
)
mapper.add_downconverters(physical_dig, physical_dnc)
mapper.set_lo_frequencies([physical_awg, physical_dnc], lo_frequency)

In [5]:
program = qcs.Program()

# define the pulse frequency as an array with three values
freq = qcs.Array("rf", value=[5.1e9, 5.2e9, 5.3e9])

# instantiate the RF waveform
waveform = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 0.25, freq)

program.add_waveform(waveform, virtual_awgs)

# add an acquisition with an integration filter that matches those frequencies
program.add_acquisition(qcs.IntegrationFilter(waveform), virtual_digs)

program.draw()

In [6]:
program = qcs.Program()

# instantiate the RF waveforms
waveform_1 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 0.25, 5.1e9)
waveform_2 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 0.25, 5.2e9)
waveform_3 = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 0.25, 5.3e9)

# add them to the program
program.add_waveform(waveform_1, virtual_awgs[0])
program.add_waveform(waveform_2, virtual_awgs[1])
program.add_waveform(waveform_3, virtual_awgs[2])

# add acquisitions
program.add_acquisition(qcs.IntegrationFilter(waveform_1), virtual_digs[0])
program.add_acquisition(qcs.IntegrationFilter(waveform_2), virtual_digs[1])
program.add_acquisition(qcs.IntegrationFilter(waveform_3), virtual_digs[2])

program.draw()

In [7]:
program.render(channel_subplots=False, mapper=mapper)

In [8]:
if run_on_hw:
    # initialize the backend pass
    backend = qcs.HclBackend(channel_mapper=mapper)
    # the executor returns the program populated with results
    program = qcs.Executor(backend).execute(program)
    # (optional) export the data to an HDF5 file
    program.to_hdf5("multiplexed_program.hdf5")

# we are loading a previously run program here for this example
program = qcs.load("multiplexed_program.hdf5")

In [9]:
program.plot_trace(channel_subplots=False)

In [10]:
program.plot_spectrum(channel_subplots=False)

In [11]:
program.plot_iq(plot_type="scatter", channel_subplots=False)